In [1]:
# written 2/9/22 by @ caramnix -->modified 3/30/22
# modified from Connectedness_Fowler2006.ipynb 
import os, json
import xmltodict
import numpy as np
import pandas as pd
import math

In [ ]:
#read in bill_dict

In [34]:
#now can read in easily! House 116 Data 
os.chdir("/Users/caranix/Library/CloudStorage/OneDrive-TheOhioStateUniversity/Social Influence/Data/Twitter/115/115_House")
f = open('house_115_tweets/Twitter_dict_115th_house_short.json')
Twitter_Dict_H_115 = json.load(f)



In [35]:
#read in twitter handles data- note the handles were updated (read: corrected) after 1 run 
#MCdat= pd.read_csv("/Users/caranix/Library/CloudStorage/OneDrive-TheOhioStateUniversity/Social Influence/Data/Twitter/116/moc116_joined_u.csv")
#Sendat= MCdat.loc[MCdat['chamber'] == "Senate"]

MCdat= pd.read_csv("/Users/caranix/Library/CloudStorage/OneDrive-TheOhioStateUniversity/Social Influence/Data/Twitter/115/115_congress.csv")

#initialize w/ handles so can check if mentioned 
legd= {} 
for i in range(0, len(MCdat)): 
    legd[MCdat["screen_name"].iloc[i]] = []
    
#more_accounts =  ["joekennedy",  "JeffVanDrew", "HornForCongress"] 
#for i in range(len(more_accounts)):
#    legd[more_accounts[i]] = [] 

In [36]:
master_data= pd.read_csv("/Users/caranix/Library/CloudStorage/OneDrive-TheOhioStateUniversity/Social Influence/Data/Congress/115/115house_username_ID.csv")


In [37]:
master_data

Unnamed: 0 district  meta_id      user_id      screen_name  congress  \
0             1    AK-AL  Y000033   37007274.0      repdonyoung     115.0   
1             2    AL-01  B001289   42481696.0     BradleyByrne     115.0   
2             3    AL-02  R000591  224294785.0    RepMarthaRoby     115.0   
3             4    AL-03  R000575   33977070.0  RepMikeRogersAL     115.0   
4             5    AL-04  A000055   76452765.0  Robert_Aderholt     115.0   
..          ...      ...      ...          ...              ...       ...   
502         503    VI-AL      NaN          NaN              NaN       NaN   
503         504    MP-AL      NaN          NaN              NaN       NaN   
504         505    NM-02      NaN          NaN              NaN       NaN   
505         506    DC-AL      NaN          NaN              NaN       NaN   
506         507    PA-14      NaN          NaN              NaN       NaN   

    chamber    icpsr  state_icpsr  district_code  ...  \
0     House  14066.0         81.0            1.0  ...   
1     House  21376.0         41.0            1.0  ...   
2     House  21192.0         41.0            2.0  ...   
3     House  20301.0         41.0            3.0  ...   
4     House  29701.0         41.0            4.0  ...   
..      ...      ...          ...            ...  ...   
502     NaN      NaN          NaN            NaN  ...   
503     NaN      NaN          NaN            NaN  ...   
504     NaN      NaN          NaN            NaN  ...   
505     NaN      NaN          NaN            NaN  ...   
506     NaN      NaN          NaN            NaN  ...   

    nominate_number_of_votes  nominate_number_of_errors  conditional  \
0                      926.0                       91.0          NaN   
1                      956.0                       19.0          NaN   
2                      939.0                       23.0          NaN   
3                      944.0                       64.0          NaN   
4                      919.0                       21.0          NaN   
..                       ...                        ...          ...   
502                      NaN                        NaN          NaN   
503                      NaN                        NaN          NaN   
504                      NaN                        NaN          NaN   
505                      NaN                        NaN          NaN   
506                      NaN                        NaN          NaN   

     nokken_poole_dim1 nokken_poole_dim2     X  Last.Name  Party  \
0                0.277             0.315  1256      YOUNG      R   
1                0.577             0.429  2197      BYRNE      R   
2                0.410             0.596  1986       ROBY      R   
3                0.397             0.482  1704     ROGERS      R   
4                0.395             0.605  1460   ADERHOLT      R   
..                 ...               ...   ...        ...    ...   
502                NaN               NaN  2274   PLASKETT      D   
503                NaN               NaN  1962     SABLAN      D   
504                NaN               NaN  1738     PEARCE      R   
505                NaN               NaN   868     NORTON      D   
506                NaN               NaN   316      DOYLE      D   

                                             Full.Name    ID  
0                      Rep. Young, Don [R-AK-At Large]  1256  
1                         Rep. Byrne, Bradley [R-AL-1]  2197  
2                           Rep. Roby, Martha [R-AL-2]  1986  
3                        Rep. Rogers, Mike D. [R-AL-3]  1704  
4                    Rep. Aderholt, Robert B. [R-AL-4]  1460  
..                                                 ...   ...  
502           Del. Plaskett, Stacey E. [D-VI-At Large]  2274  
503  Del. Sablan, Gregorio Kilili Camacho [D-MP-At ...  1962  
504                       Rep. Pearce, Stevan [R-NM-2]  1738  
505        Del. Norton, Eleanor Holmes [D-DC-At Large]   868  
506                 

In [38]:
u_id_nums= np.unique(master_data["ID"])

In [39]:
master_data.loc[master_data["screen_name"] == "repdonyoung"]["ID"]

0    1256
Name: ID, dtype: int64

In [40]:
def get_id_from_handle(handle):
    try:
        return(master_data.loc[master_data["screen_name"] == handle]["ID"].to_numpy()[0])
    except IndexError: 
        if handle == "repdonyoung": 
            return(1256)
        if handle == "RepArmstrongND": 
            return(2417)
        if handle == "PeterWelch": 
            return(1879)
        if handle == "RepDustyJohnson": 
            return(2439)
        if handle == "RepLizCheney": 
            return(2356)
        if handle == "RepLBR": 
            return(2313)
    

In [41]:
#written on 4/1/21 --? modfied on 4/26/21 -->and again on 3/23/22
#build w_ij, or the weighted quantity of cosponsored bills 
u_id_nums= np.unique(master_data["ID"])
#probs = np.array([2313, 1256, 2417,1879,2439, 2356])
#u_id_nums = np.append(u_id_nums,probs)

w_ij = pd.DataFrame(index=u_id_nums, columns= u_id_nums)
w_ij = w_ij.fillna(0)
for key in Twitter_Dict_H_115: 
    try: 
        #print(Tweet_Dict[key])
        author_handle= Twitter_Dict_H_115[key]['author']
    except KeyError: 
        print(key)
        print(Twitter_Dict_H_115[key])
        pass
    author_id= int(get_id_from_handle(author_handle))
    n_cospos= len(Twitter_Dict_H_115[key]['mentions'])
    if n_cospos == 0: 
        pass 
    else: 
        for i in range(0,n_cospos): 
            mention_username= Twitter_Dict_H_115[key]['mentions'][str(i)]
            print(mention_username)
            mention_id= int(get_id_from_handle(mention_username))
            print(mention_id, author_id)
            w_ij.loc[mention_id,author_id]= w_ij.loc[mention_id,author_id] + (1/n_cospos)
            

RepTimRyan
1756 2169
RepDelBene
2096 2169
RepTimRyan
1756 2169
RepDarrenSoto
2319 2169
RepKathleenRice
2262 2169
RepGallagher
2355 2169
RepNewhouse
2275 2169
RepStefanik
2263 2169
RepArrington
2350 2169
RepDerekKilmer
2169 2169
rep_stevewomack
1991 2169
RepKenBuck
2233 2169
RepAdamSmith
1528 2169
RepDerekKilmer
2169 2169
RepNewhouse
2275 2169
RepNewhouse
2275 2169
RepNewhouse
2275 2169
RepNewhouse
2275 2169
CongressmanGT
1799 2169
RepRonKind
1498 2169
RepDerekKilmer
2169 2169
RepArrington
2350 2169
RepMikeCoffman
1912 2169
RepAnnieKuster
2145 2169
rep_stevewomack
1991 2169
rep_stevewomack
1991 2169
rep_stevewomack
1991 2169
rep_stevewomack
1991 2169
rep_stevewomack
1991 2169
rep_stevewomack
1991 2169
RepDerekKilmer
2169 2169
RepVeasey
2166 2169
RepStefanik
2263 2169
RepDerekKilmer
2169 2169
RepDerekKilmer
2169 2169
RepDerekKilmer
2169 2169
RepDerekKilmer
2169 2169
RepDerekKilmer
2169 2169
RepStefanik
2263 2169
RepDanKildee
2134 2169
RepStefanik
2263 2169
RepDanKildee
2134 2169
Congress

RepMcEachin
2352 2352
RepMcEachin
2352 2352
RepMcEachin
2352 2352
RepLowenthal
2111 2352
RepMcEachin
2352 2352
RepDonBeyer
2272 2352
RepRaulGrijalva
1708 2352
RepLowenthal
2111 2352
RepBarragan
2311 2352
RepDonBeyer
2272 2352
RepJimmyGomez
70 2352
RepMcEachin
2352 2352
RepMcEachin
2352 2352
RepMcEachin
2352 2352
RepMcEachin
2352 2352
BobbyScott
1037 2352
RepTimRyan
1756 2352
RepBarragan
2311 2352
RepMcEachin
2352 2352
RepMcEachin
2352 2352
RepDonBeyer
2272 2352
BobbyScott
1037 2352
RepMcEachin
2352 2352
GerryConnolly
1959 2352
RepDianaDeGette
1479 2352
RepMcEachin
2352 2352
RepMcEachin
2352 2352
RepMcEachin
2352 2352
RepBonnie
2259 2352
RepEspaillat
2342 2352
RepMaxineWaters
1205 2352
RepMcEachin
2352 2352
RepMcEachin
2352 2352
RepMcEachin
2352 2352
RepMcEachin
2352 2352
RepWilson
2004 2352
RepRaulGrijalva
1708 2352
RepMcEachin
2352 2352
BobbyScott
1037 2352
RepMcEachin
2352 2352
RepMcEachin
2352 2352
RepMcEachin
2352 2352
RepMcEachin
2352 2352
RepMcEachin
2352 2352
RepMcEachin
2352 23

RepMcEachin
2352 2352
RepMikeRogersAL
1704 1704
SteveScalise
1892 1704
JudgeTedPoe
1802 1704
RepMoBrooks
1987 1704
RepMikeRogersAL
1704 1704
RepLouBarletta
2054 1704
RepMikeRogersAL
1704 1704
RepMikeRogersAL
1704 1704
JudgeTedPoe
1802 1704
repjimcooper
231 1704
SteveScalise
1892 1704
RepMikeRogersAL
1704 1704
RepMullin
2156 1704
SteveScalise
1892 1704
RepMcCaul
1804 1704
SteveScalise
1892 1704
RepTerriSewell
1988 1704
RepMikeRogersAL
1704 1704
RepMikeRogersAL
1704 1704
RepMGriffith
2070 1704
RepDavidRouzer
2256 1704
DrNealDunnFL2
2315 1704
RepGusBilirakis
1838 1704
RepMattGaetz
2314 1704
RepMoBrooks
1987 1704
RepAndyBarr
2131 1704
RepAdams
2201 2134
RepDanKildee
2134 2134
janschakowsky
1588 2134
RepCohen
1878 2134
repdinatitus
1940 2134
RepSarbanes
1854 2134
RepDanKildee
2134 2134
RepCheri
2127 2134
SpeakerRyan
1560 2134
RepDwightEvans
2051 2134
RepTimWalz
1856 2134
RepLoisFrankel
2119 2134
RepSpeier
1890 2134
RepRobinKelly
2190 2134
RepJaredPolis
1910 2134
RepDanKildee
2134 2134
RepMo

RepDanKildee
2134 2134
RepJohnConyers
2375 2134
repsandylevin
683 2134
RepDebDingell
2251 2134
RepDanKildee
2134 2134
RepDanKildee
2134 2134
RepAndreCarson
1889 2134
SpeakerRyan
1560 2134
RepDanKildee
2134 2134
janschakowsky
1588 2134
repsandylevin
683 2134
RepMcGovern
1504 2134
RepJackBergman
2333 2134
DonaldNorcross
2202 2134
RepRaskin
2332 2134
RepAnnaEshoo
355 2134
RepJackBergman
2333 2134
FrankPallone
887 2134
RepMaxineWaters
1205 2134
NitaLowey
709 2134
RepRichardNeal
854 2134
RepDanKildee
2134 2134
gracenapolitano
1602 2134
RepRaskin
2332 2134
RepCartwright
2345 2134
RepDebDingell
2251 2134
RepTedLieu
2230 2134
RepCicilline
2055 2134
RepCheri
2127 2134
RepDanKildee
2134 2196
RepDanKildee
2134 2134
RepKarenBass
1996 2134
RepJeffries
2149 2134
RepBobbyRush
1003 2134
RepDebDingell
2251 2134
RepYvetteClarke
1864 2134
RepAnthonyBrown
2331 2134
RepMcGovern
1504 2134
RepRubenGallego
2226 2134
RepRaulGrijalva
1708 2134
RepDanKildee
2134 2134
FrankPallone
887 2134
RepLujanGrisham
2146 21

RobinLynneKelly
2190 2190
RepMikeQuigley
1967 2190
RepDannyDavis
1477 2190
RobinLynneKelly
2190 2190
RepDannyDavis
1477 2190
RobinLynneKelly
2190 2190
SpeakerRyan
1560 2190
RobinLynneKelly
2190 2190
SpeakerRyan
1560 2190
RobinLynneKelly
2190 2190
RobinLynneKelly
2190 2190
RepMaloney
729 2190
RobinLynneKelly
2190 2190
SpeakerRyan
1560 2190
tedlieu
2230 2190
RepRobinKelly
2190 2190
RepThompson
1593 2190
RepDeSaulnier
2227 2190
RepRobinKelly
2190 2190
RepRobinKelly
2190 2190
RepWilson
2004 2190
RepRobinKelly
2190 2190
RepWilson
2004 2190
RepLawrence
2252 2190
RepMarciaFudge
1895 2190
RepRobinKelly
2190 2190
RepRobinKelly
2190 2190
NydiaVelazquez
1184 2190
NydiaVelazquez
1184 2190
RepGutierrez
478 2190
RepBeatty
2153 2190
SpeakerRyan
1560 2190
RepRobinKelly
2190 2190
RepRobinKelly
2190 2190
SpeakerRyan
1560 2190
RepCicilline
2055 2190
RepCicilline
2055 2190
RepCicilline
2055 2190
RepCicilline
2055 2190
SpeakerRyan
1560 2190
RepRobinKelly
2190 2190
RepRobinKelly
2190 2190
SteveScalise
1892 

...

2338 2202
RepLanceNJ7
1936 2202
RepAnnieKuster
2145 2202
RepTomMacArthur
2258 2202
RepBrianFitz
1469 2202
DonaldNorcross
2202 2202
RepMarcyKaptur
616 2202
RepJeffries
2149 2202
USRepRickNolan
867 2202
RepDebDingell
2251 2202
RepTerriSewell
1988 2202
DonaldNorcross
2202 2202
RepJohnLarson
1583 2202
RepAnnieKuster
2145 2202
RepTomMacArthur
2258 2202
DonaldNorcross
2202 2202
RepBrianFitz
1469 2202
RepAnnieKuster
2145 2202
RepTomMacArthur
2258 2202
RepBrianFitz
1469 2202
RepAnnieKuster
2145 2202
RepTomMacArthur
2258 2202
DonaldNorcross
2202 2202
RepBrianFitz
1469 2202
RepAnnieKuster
2145 2202
RepTomMacArthur
2258 2202
DonaldNorcross
2202 2202
RepBrianFitz
1469 2202
DonaldNorcross
2202 2202
RepRaulGrijalva
1708 2202
DonaldNorcross
2202 2202
RepKihuen
2340 2202
DonaldNorcross
2202 2202
RepTomMacArthur
2258 2202
RepAnnieKuster
2145 2202
RepTomMacArthur
2258 2202
RepBrianFitz
1469 2202
SteveScalise
1892 2202
DonaldNorcross
2202 2202
DonaldNorcross
2202 2202
DonaldNorcross
2202 2202
RoKhanna
23

chelliepingree
1927 1501
RepBarbaraLee
1501 1501
RepBarbaraLee
1501 1501
RepBarbaraLee
1501 1501
keithellison
1857 1501
RepTimRyan
1756 1501
RepBarbaraLee
1501 1501
RepBarbaraLee
1501 1501
RepRobinKelly
2190 1501
SpeakerRyan
1560 1501
RepBarbaraLee
1501 1501
RepBarbaraLee
1501 1501
sethmoulton
2246 1501
RepBarbaraLee
1501 1501
RepRoybalAllard
997 1501
RepBarbaraLee
1501 1501
chelliepingree
1927 1501
RepBarbaraLee
1501 1501
RepAdamSchiff
1635 1501
RepBarbaraLee
1501 1501
RepBarbaraLee
1501 1501
RepBarbaraLee
1501 1501
RepBarbaraLee
1501 1501
RepBarbaraLee
1501 1501
RepBarbaraLee
1501 1501
RepJayapal
2354 1501
RepJohnYarmuth
1853 1501
repmarkpocan
2171 1501
RepBarbaraLee
1501 1501
RepJohnYarmuth
1853 1501
RepJayapal
2354 1501
RepLeeZeldin
2261 1501
RepBarbaraLee
1501 1501
RepBarbaraLee
1501 1501
RepBarbaraLee
1501 1501
RepBarbaraLee
1501 1501
repjohnlewis
688 1501
SpeakerRyan
1560 1501
RepJayapal
2354 1501
RepBarbaraLee
1501 1501
RepBarbaraLee
1501 1501
RepBarbaraLee
1501 1501
repmarkpoc

RepBarbaraLee
1501 1501
RepBonnie
2259 1501
RepBarbaraLee
1501 1501
janschakowsky
1588 1501
JacksonLeeTX18
588 1501
RepEspaillat
2342 1501
RepMarkTakano
2110 1501
RepBonnie
2259 1501
RepWilson
2004 1501
RepJohnDelaney
2133 1501
chelliepingree
1927 1501
RepLoisFrankel
2119 1501
RepYvetteClarke
1864 1501
RepHanabusa
2010 1501
RepLawrence
2252 1501
RepBonnie
2259 1501
repjohnlewis
688 1501
RepAdamSchiff
1635 1501
RepBarbaraLee
1501 1501
RepLoisFrankel
2119 1501
RepBarbaraLee
1501 1501
RepJerryNadler
850 1501
RepBarbaraLee
1501 1501
RepJerryNadler
850 1501
RepBarbaraLee
1501 1501
RepKevinBrady
1468 1501
RepJerryNadler
850 1501
RepCummings
256 1501
BillPascrell
1510 1501
repjohnlewis
688 1501
janschakowsky
1588 1501
RepBarbaraLee
1501 1501
janschakowsky
1588 1501
RepBarbaraLee
1501 1501
RepBarbaraLee
1501 1501
janschakowsky
1588 1501
RepBarbaraLee
1501 1501
janschakowsky
1588 1501
louiseslaughter
1069 1501
RepBarbaraLee
1501 1501
JoaquinCastrotx
2163 1501
RepZoeLofgren
701 1501
RepAndreCars

RepSwalwell
2104 2119
RepEliotEngel
344 2119
RepCheri
2127 2119
SpeakerRyan
1560 2119
RepLoisFrankel
2119 2119
RepCheri
2127 2119
BillPascrell
1510 2119
RepCheri
2127 2119
RepJohnLarson
1583 2119
rosadelauro
281 2119
janschakowsky
1588 2119
RepLoisFrankel
2119 2119
RepJudyChu
1970 2119
RepJayapal
2354 2119
MarioDB
1717 2119
RepLoisFrankel
2119 2119
RepLloydDoggett
303 2119
DorisMatsui
1814 2119
janschakowsky
1588 2119
RepJohnYarmuth
1853 2119
SpeakerRyan
1560 2119
RepWilson
2004 2119
RepLoisFrankel
2119 2119
RepLoisFrankel
2119 2119
RepDanKildee
2134 2119
SpeakerRyan
1560 2119
RepLoisFrankel
2119 2119
RepHankJohnson
1843 2119
RepWilson
2004 2119
RepLoisFrankel
2119 2119
RepLoisFrankel
2119 2119
RepLoisFrankel
2119 2119
RepLoisFrankel
2119 2119
RepSpeier
1890 2119
janschakowsky
1588 2119
RosLehtinen
985 2119
RepPeteAguilar
2229 2119
RepCarbajal
2310 2119
RepRobinKelly
2190 2119
SpeakerRyan
1560 2119
SpeakerRyan
1560 2119
RepThompson
1593 2119
RepLoisFrankel
2119 2119
RepLoisFrankel
2119

RepLoisFrankel
2119 2119
RepLoisFrankel
2119 2119
RepAnthonyBrown
2331 2119
RepSeanMaloney
2150 2119
USRepKeating
2025 2119
NitaLowey
709 2119
RepAnnieKuster
2145 2119
RepSpeier
1890 2119
RepLoisFrankel
2119 2119
RepJerryNadler
850 2119
RepJohnYarmuth
1853 2119
RepJerryNadler
850 2119
RepLoisFrankel
2119 2119
RepJuanVargas
2112 2119
RepCheri
2127 2119
FrankPallone
887 2119
RepRobinKelly
2190 2119
RepTedDeutch
1976 2119
SteveKingIA
1724 2119
RepCummings
256 2119
rosadelauro
281 2119
RepValDemings
2320 2119
NydiaVelazquez
1184 2119
RepMaloney
729 2119
RepSpeier
1890 2119
RepTedLieu
2230 2119
RepJerryNadler
850 2119
SpeakerRyan
1560 2119
RepEliotEngel
344 2119
RepLoisFrankel
2119 2119
RepLoisFrankel
2119 2119
AustinScottGA08
2009 2119
RepLawrence
2252 2119
RepCheri
2127 2119
AustinScottGA08
2009 2119
RepTimWalz
1856 2119
RepEliotEngel
344 2119
USRepKeating
2025 2119
RepBarbaraLee
1501 2119
RepDianaDeGette
1479 2119
RepTerriSewell
1988 2119
RepLoisFrankel
2119 2119
RepTerriSewell
1988 2119

In [27]:
get_id_from_handle("repdonyoung")

nan

In [42]:
w_ij

62          70    91    99         165   186   208   229   231   \
62    38.166667    0.000000   0.0     0   0.111111   0.0   0.0     0   0.0   
70     0.000000  377.983333   0.0     0   0.000000   0.0   0.0     0   0.0   
91     0.000000    0.000000   8.7     0   0.000000   0.0   0.0     0   0.0   
99     0.000000    0.000000   0.0     0   0.000000   0.0   0.0     0   0.0   
165    0.000000    0.000000   0.0     0  41.333333   0.0   0.0     0   0.0   
...         ...         ...   ...   ...        ...   ...   ...   ...   ...   
2371   0.000000    0.000000   0.0     0   0.000000   0.0   0.0     0   0.0   
2372   0.000000    0.000000   0.0     0   0.000000   0.0   0.0     0   0.0   
2373   0.000000    0.000000   0.0     0   0.000000   0.0   0.0     0   0.0   
2374   0.000000    0.000000   0.0     0   0.000000   0.0   0.0     0   0.0   
2375   0.000000    2.583333   0.0     0   0.000000   0.0   0.0     0   0.0   

          256   ...  2363  2367  2368  2369  2370  2371  2372  2373  2374  \
62    0.000000  ...     0   1.0   0.0     0   0.0     0   0.0     0     0   
70    1.500000  ...     0   0.0   0.0     0   0.0     0   0.0     0     0   
91    0.000000  ...     0   0.0   0.0     0   0.0     0   0.0     0     0   
99    0.000000  ...     0   0.0   0.0     0   0.0     0   0.0     0     0   
165   0.000000  ...     0   0.0   0.0     0   0.0     0   0.0     0     0   
...        ...  ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   
2371  0.000000  ...     0   0.0   0.0     0   0.0     0   0.0     0     0   
2372  0.000000  ...     0   0.0   0.0     0   0.0     0   0.5     0     0   
2373  0.000000  ...     0   0.0   0.0     0   0.0     0   0.0     0     0   
2374  0.000000  ...     0   0.0   0.0     0   0.0     0   0.0     0     0   
2375  2.833333  ...     0   0.0   0.0     0   0.0     0   0.0     0     0   

            2375  
62      0.000000  
70      1.500000  
91      0.500000  
99      0.000000  
165     0.000000  
...          ...  
2371    0.000000  
2372    0.000000  
2373    0.000000  
2374    0.000000  
2375  192.716667  

[453 rows x 453 columns]

In [43]:
w_ij.to_csv("w_ij_Twitter_house_115.csv")

In [26]:
#Bill_Dict_H_116['765HRES']

In [44]:
#now build d_ij- higher values --> less connected 
d_ij = 1/w_ij        

In [58]:
d_ij

62        70        91    99        165   186   208   229   231   \
62    0.026201       inf       inf   inf  9.000000   inf   inf   inf   inf   
70         inf  0.002646       inf   inf       inf   inf   inf   inf   inf   
91         inf       inf  0.114943   inf       inf   inf   inf   inf   inf   
99         inf       inf       inf   inf       inf   inf   inf   inf   inf   
165        inf       inf       inf   inf  0.024194   inf   inf   inf   inf   
...        ...       ...       ...   ...       ...   ...   ...   ...   ...   
2371       inf       inf       inf   inf       inf   inf   inf   inf   inf   
2372       inf       inf       inf   inf       inf   inf   inf   inf   inf   
2373       inf       inf       inf   inf       inf   inf   inf   inf   inf   
2374       inf       inf       inf   inf       inf   inf   inf   inf   inf   
2375       inf  0.387097       inf   inf       inf   inf   inf   inf   inf   

          256   ...  2363  2367  2368  2369  2370  2371  2372  2373  2374  \
62         inf  ...   inf   1.0   inf   inf   inf   inf   inf   inf   inf   
70    0.666667  ...   inf   inf   inf   inf   inf   inf   inf   inf   inf   
91         inf  ...   inf   inf   inf   inf   inf   inf   inf   inf   inf   
99         inf  ...   inf   inf   inf   inf   inf   inf   inf   inf   inf   
165        inf  ...   inf   inf   inf   inf   inf   inf   inf   inf   inf   
...        ...  ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   
2371       inf  ...   inf   inf   inf   inf   inf   inf   inf   inf   inf   
2372       inf  ...   inf   inf   inf   inf   inf   inf   2.0   inf   inf   
2373       inf  ...   inf   inf   inf   inf   inf   inf   inf   inf   inf   
2374       inf  ...   inf   inf   inf   inf   inf   inf   inf   inf   inf   
2375  0.352941  ...   inf   inf   inf   inf   inf   inf   inf   inf   inf   

          2375  
62         inf  
70    0.666667  
91    2.000000  
99         inf  
165        inf  
...        ...  
2371       inf  
2372       inf  
2373       inf  
2374       inf  
2375  0.005189  

[453 rows x 453 columns]

In [59]:
d_ij.to_csv("d_ij_Twitter_house_115.csv")

In [46]:
#https://www.algorithms-and-technologies.com/dijkstra/python
def dijkstra(graph, start):
    """
    Implementation of dijkstra using adjacency matrix.
    This returns an array containing the length of the shortest path from the start node to each other node.
    It is only guaranteed to return correct results if there are no negative edges in the graph. Positive cycles are fine.
    This has a runtime of O(|V|^2) (|V| = number of Nodes), for a faster implementation see @see ../fast/Dijkstra.java (using adjacency lists)

    :param graph: an adjacency-matrix-representation of the graph where (x,y) is the weight of the edge or 0 if there is no edge.
    :param start: the node to start from.
    :return: an array containing the shortest distances from the given start node to each other node
    """
    # This contains the distances from the start node to all other nodes
    distances = [float("inf") for _ in range(len(graph))]

    # This contains whether a node was already visited
    visited = [False for _ in range(len(graph))]

    # The distance from the start node to itself is of course 0
    distances[start] = 0

    # While there are nodes left to visit...
    while True:

        # ... find the node with the currently shortest distance from the start node...
        shortest_distance = float("inf")
        shortest_index = -1
        for i in range(len(graph)):
            # ... by going through all nodes that haven't been visited yet
            if distances[i] < shortest_distance and not visited[i]:
                shortest_distance = distances[i]
                shortest_index = i

        # print("Visiting node " + str(shortest_index) + " with current distance " + str(shortest_distance))

        if shortest_index == -1:
            # There was no node not yet visited --> We are done
            return distances

        # ...then, for all neighboring nodes that haven't been visited yet....
        for i in range(len(graph[shortest_index])):
            # ...if the path over this edge is shorter...
            if graph[shortest_index][i] != 0 and distances[i] > distances[shortest_index] + graph[shortest_index][i]:
                # ...Save this path as new shortest path.
                distances[i] = distances[shortest_index] + graph[shortest_index][i]
                # print("Updating distance of node " + str(i) + " to " + str(distances[i]))

        # Lastly, note that we are finished with this node.
        visited[shortest_index] = True
        # print("Visited nodes: " + str(visited))
        # print("Currently lowest distances: " + str(distances))


In [47]:
# dijkstras provides a matrix of shortest distances between each pair of legislators in the whole network 
dijkstra_mat = pd.DataFrame(index=u_id_nums, columns= u_id_nums)
dijkstra_mat = dijkstra_mat.fillna(0)

In [48]:
for i in range(0, len(u_id_nums)):     
    dijkstra_mat.iloc[i] = dijkstra(d_ij.to_numpy(),i)

In [49]:
dijkstra_mat

62        70        91    99        165       186       208   229   \
62    0.000000  0.745814  1.141050   inf  0.840398  0.908625  1.003361   inf   
70    0.537553  0.000000  0.678272   inf  0.377620  0.383530  0.540583   inf   
91    0.731354  0.579047  0.000000   inf  0.571421  0.639647  0.734384   inf   
99         inf       inf       inf   0.0       inf       inf       inf   inf   
165   0.243481  0.091174  0.384201   inf  0.000000  0.151775  0.246512   inf   
...        ...       ...       ...   ...       ...       ...       ...   ...   
2371       inf       inf       inf   inf       inf       inf       inf   inf   
2372  0.619192  0.466885  0.759911   inf  0.459259  0.527485  0.622222   inf   
2373       inf       inf       inf   inf       inf       inf       inf   inf   
2374       inf       inf       inf   inf       inf       inf       inf   inf   
2375  0.511380  0.198029  0.652099   inf  0.351447  0.342146  0.514410   inf   

          231       256   ...  2363      2367      2368  2369      2370  2371  \
62    1.056158  0.806381  ...   inf  0.970144  0.837844   inf  0.914472   inf   
70    0.487238  0.226444  ...   inf  0.401224  0.375066   inf  0.435356   inf   
91    0.914328  0.634384  ...   inf  0.784384  0.568867   inf  0.645495   inf   
99         inf       inf  ...   inf       inf       inf   inf       inf   inf   
165   0.426456  0.146512  ...   inf  0.296512  0.080994   inf  0.157623   inf   
...        ...       ...  ...   ...       ...       ...   ...       ...   ...   
2371       inf       inf  ...   inf       inf       inf   inf       inf   0.0   
2372  0.802166  0.522222  ...   inf  0.672222  0.456705   inf  0.533333   inf   
2373       inf       inf  ...   inf       inf       inf   inf       inf   inf   
2374       inf       inf  ...   inf       inf       inf   inf       inf   inf   
2375  0.405342  0.185060  ...   inf  0.356352  0.348893   inf  0.353461   inf   

          2372  2373  2374      2375  
62    1.977228   inf   inf  0.729964  
70    1.521407   inf   inf  0.150027  
91    1.711762   inf   inf  0.619888  
99         inf   inf   inf       inf  
165   1.227336   inf   inf  0.132015  
...        ...   ...   ...       ...  
2371       inf   inf   inf       inf  
2372  0.000000   inf   inf  0.507726  
2373       inf   0.0   inf       inf  
2374       inf   inf   0.0       inf  
2375  1.495234   inf   inf  0.000000  

[453 rows x 453 columns]

In [50]:
dijkstra_mat= dijkstra_mat.replace([np.inf, -np.inf], np.nan) 

In [51]:
maxElement1 = max(np.amax(dijkstra_mat, 1))
maxElement0 = max(np.amax(dijkstra_mat, 0))

In [52]:
maxElement1 = max(np.amax(dijkstra_mat, 1))
dijkstra_mat= dijkstra_mat.replace([np.nan], maxElement1 +1) 

In [53]:
dijkstra_mat

62        70        91        99        165       186       208   \
62    0.000000  0.745814  1.141050  4.892666  0.840398  0.908625  1.003361   
70    0.537553  0.000000  0.678272  4.892666  0.377620  0.383530  0.540583   
91    0.731354  0.579047  0.000000  4.892666  0.571421  0.639647  0.734384   
99    4.892666  4.892666  4.892666  0.000000  4.892666  4.892666  4.892666   
165   0.243481  0.091174  0.384201  4.892666  0.000000  0.151775  0.246512   
...        ...       ...       ...       ...       ...       ...       ...   
2371  4.892666  4.892666  4.892666  4.892666  4.892666  4.892666  4.892666   
2372  0.619192  0.466885  0.759911  4.892666  0.459259  0.527485  0.622222   
2373  4.892666  4.892666  4.892666  4.892666  4.892666  4.892666  4.892666   
2374  4.892666  4.892666  4.892666  4.892666  4.892666  4.892666  4.892666   
2375  0.511380  0.198029  0.652099  4.892666  0.351447  0.342146  0.514410   

          229       231       256   ...      2363      2367      2368  \
62    4.892666  1.056158  0.806381  ...  4.892666  0.970144  0.837844   
70    4.892666  0.487238  0.226444  ...  4.892666  0.401224  0.375066   
91    4.892666  0.914328  0.634384  ...  4.892666  0.784384  0.568867   
99    4.892666  4.892666  4.892666  ...  4.892666  4.892666  4.892666   
165   4.892666  0.426456  0.146512  ...  4.892666  0.296512  0.080994   
...        ...       ...       ...  ...       ...       ...       ...   
2371  4.892666  4.892666  4.892666  ...  4.892666  4.892666  4.892666   
2372  4.892666  0.802166  0.522222  ...  4.892666  0.672222  0.456705   
2373  4.892666  4.892666  4.892666  ...  4.892666  4.892666  4.892666   
2374  4.892666  4.892666  4.892666  ...  4.892666  4.892666  4.892666   
2375  4.892666  0.405342  0.185060  ...  4.892666  0.356352  0.348893   

          2369      2370      2371      2372      2373      2374      2375  
62    4.892666  0.914472  4.892666  1.977228  4.892666  4.892666  0.729964  
70    4.892666  0.435356  4.892666  1.521407  4.892666  4.892666  0.150027  
91    4.892666  0.645495  4.892666  1.711762  4.892666  4.892666  0.619888  
99    4.892666  4.892666  4.892666  4.892666  4.892666  4.892666  4.892666  
165   4.892666  0.157623  4.892666  1.227336  4.892666  4.892666  0.132015  
...        ...       ...       ...       ...       ...       ...       ...  
2371  4.892666  4.892666  0.000000  4.892666  4.892666  4.892666  4.892666  
2372  4.892666  0.533333  4.892666  0.000000  4.892666  4.892666  0.507726  
2373  4.892666  4.892666  4.892666  4.892666  0.000000  4.892666  4.892666  
2374  4.892666  4.892666  4.892666  4.892666  4.892666  0.000000  4.892666  
2375  4.892666  0.353461  4.892666  1.495234  4.892666  4.892666  0.000000  

[453 rows x 453 columns]

In [54]:
dijkstra_mat.to_csv("dijkstra_mat_Twitter_house_115.csv")

In [55]:
#this does what you want- sums rows (row sum is how connected legislator i is to everone else)
connectedness_score = pd.DataFrame(index=u_id_nums, columns= ["Connectedness"]) #select command + "" ==> quoting selection
num= len(u_id_nums)-1 
for i in range(0,len(dijkstra_mat)): 
    denom= sum(dijkstra_mat.iloc[i])
    connectedness_score.iloc[i]= num/denom 


In [56]:
connectedness_score

Connectedness
62        0.633523
70        0.867459
91        0.715278
99        0.204388
165       1.008344
...            ...
2371      0.204388
2372      0.769093
2373      0.204388
2374      0.204388
2375      0.886278

[453 rows x 1 columns]

In [57]:
connectedness_score.to_csv("connectedness_house_twitter_115.csv")